# Segmenting and Clustering Neighborhoods in Toronto 

## Part 1: Collecting and cleaning neighborhood's data
First, after importing the necessary libraries, we have to download the data from Wikipedia and select the neighborhoods' table.

In [1]:
import folium
import pandas as pd
import os
import requests
import seaborn as sns

from sklearn.cluster import KMeans

pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

In [2]:
toronto = pd.read_html(
    "https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M", 
    match="Neighbourhood"
)[0]
toronto.columns = ["Postal Code", "Borough", "Neighborhood"]
print(toronto.shape)
toronto.head()

(180, 3)


Postal Code           Borough               Neighborhood
0         M1A      Not assigned               Not assigned
1         M2A      Not assigned               Not assigned
2         M3A        North York                  Parkwoods
3         M4A        North York           Victoria Village
4         M5A  Downtown Toronto  Regent Park, Harbourfront

Then, let's do some clean up on the dataframe, by applying the following steps:
- drop all rows not assigned to a `Bourough`;
- `Not assigned` neighborhoods should have the same value as the `Borough`;
- and make sure all postal codes are unique.

In [3]:
def fix_nb(entry):
    if entry["Neighborhood"] == "Not Assigned":
        entry["Neighborhood"] = entry["Borough"]
    return entry

# ignore 'Not assigned' boroughes
toronto = toronto[toronto['Borough'] != "Not assigned"]

# Fix 'Not assigned' neighborhoods
toronto = toronto.apply(fix_nb, axis=1)

# Check for neighborhoods uniqueness
num_postal_codes = len(toronto['Postal Code'].unique())
if num_postal_codes == toronto.shape[0]:
    print('All postal codes in the dataframe contains a single neighborhood')
else:
    print('There are more than one neighborhood for some postal codes')
    
toronto.head()

All postal codes in the dataframe contains a single neighborhood


Postal Code           Borough                                 Neighborhood
2         M3A        North York                                    Parkwoods
3         M4A        North York                             Victoria Village
4         M5A  Downtown Toronto                    Regent Park, Harbourfront
5         M6A        North York             Lawrence Manor, Lawrence Heights
6         M7A  Downtown Toronto  Queen's Park, Ontario Provincial Government

In [4]:
print(toronto.shape)

(103, 3)


## Part 2: Adding up geolocation data

Let's download the geospatial data and merge it to the neighborhoods' dataframe

In [5]:
geospatial_data = pd.read_csv("https://cocl.us/Geospatial_data")

In [6]:
toronto = pd.merge(toronto, geospatial_data, on='Postal Code')
toronto.head(15)

Postal Code           Borough  \
0          M3A        North York   
1          M4A        North York   
2          M5A  Downtown Toronto   
3          M6A        North York   
4          M7A  Downtown Toronto   
5          M9A         Etobicoke   
6          M1B       Scarborough   
7          M3B        North York   
8          M4B         East York   
9          M5B  Downtown Toronto   
10         M6B        North York   
11         M9B         Etobicoke   
12         M1C       Scarborough   
13         M3C        North York   
14         M4C         East York   

                                         Neighborhood   Latitude  Longitude  
0                                           Parkwoods  43.753259 -79.329656  
1                                    Victoria Village  43.725882 -79.315572  
2                           Regent Park, Harbourfront  43.654260 -79.360636  
3                    Lawrence Manor, Lawrence Heights  43.718518 -79.464763  
4         Queen's Park, Ontario Provincial Government  43.662301 -79.389494  
5             Islington Avenue, Humber Valley Village  43.667856 -79.532242  
6                                      Malvern, Rouge  43.806686 -79.194353  
7                                           Don Mills  43.745906 -79.352188  
8                     Parkview Hill, Woodbine Gardens  43.706397 -79.309937  
9                            Garden District, Ryerson  43.657162 -79.378937  
10                                          Glencairn  43.709577 -79.445073  
11  West Deane Park, Princess Gardens, Martin Grov...  43.650943 -79.554724  
12             Rouge Hill, Port Union, Highland Creek  43.784535 -79.160497  
13                                          Don Mills  43.725900 -79.340923  
14                                   Woodbine Heights  43.695344 -79.318389

In [7]:
# Optional. Store/Retrieve Toronto's Dataframe, to save time
# toronto.to_csv("toronto.csv")
# toronto = pd.read_csv("toronto.csv", index_col=0)

In [8]:
toronto.head()

Postal Code           Borough                                 Neighborhood  \
0         M3A        North York                                    Parkwoods   
1         M4A        North York                             Victoria Village   
2         M5A  Downtown Toronto                    Regent Park, Harbourfront   
3         M6A        North York             Lawrence Manor, Lawrence Heights   
4         M7A  Downtown Toronto  Queen's Park, Ontario Provincial Government   

    Latitude  Longitude  
0  43.753259 -79.329656  
1  43.725882 -79.315572  
2  43.654260 -79.360636  
3  43.718518 -79.464763  
4  43.662301 -79.389494

## Part 3: Getting venues data and clustering the neighborhoods

First, let's plot Toronto's neighborhoods on a map

In [9]:
lat_avg, lng_avg = toronto['Latitude'].mean(), toronto['Longitude'].mean()
map_toronto = folium.Map(location=[lat_avg, lng_avg], zoom_start=11)

def add_markers_to_map(entry, city_map):
    label = folium.Popup(f"{entry['Neighborhood']}, {entry['Borough']}", parse_html=True)
    folium.CircleMarker(
        [entry["Latitude"], entry["Longitude"]],
        radius=5,
        popup=label,
        color='#7a1c1c',
        fill=True,
        fill_color='yellow',
        fill_opacity=0.6,
        parse_html=False
    ).add_to(city_map)  

    
toronto.apply(add_markers_to_map, axis=1, args=(map_toronto,))
map_toronto

Now, using the Foursquare API, let's retrieve venues data for each neighborhood

In [10]:
CLIENT_ID = os.environ.get("FOURSQUARE_CLIENT_ID")
CLIENT_SECRET = os.environ.get("FOURSQUARE_CLIENT_SECRET")
VERSION = "20180605"

def make_search_url(lat, lng, radius=500, limit=100):
    return (
        f'https://api.foursquare.com/v2/venues/explore?'
        f'client_id={CLIENT_ID}&client_secret={CLIENT_SECRET}&v={VERSION}'
        f'&ll={lat},{lng}&radius={radius}&limit={limit}'
    )

def get_venues_from_neighborhood(entry):
    url = make_search_url(entry["Latitude"], entry["Longitude"])
    results = requests.get(url).json()["response"].get("groups", [{}])[0].get("items")
    if not results:
        print(f"Could not find venues for {entry['Neighborhood']}")
    return [(
        entry["Neighborhood"],
        entry["Latitude"], 
        entry["Longitude"], 
        v['venue']['name'], 
        v['venue']['location']['lat'],
        v['venue']['location']['lng'],
        v['venue']['categories'][0]['name']) for v in results
    ]

In [11]:
# request venues for all toronto's neighborhoods
venues_lists = toronto.apply(get_venues_from_neighborhood, axis=1)

Could not find venues for Islington Avenue, Humber Valley Village
Could not find venues for Willowdale, Newtonbrook
Could not find venues for Upper Rouge


In [12]:
# flattening the the venues list and making a dataframe for them
venues = pd.DataFrame([venue for sublist in venues_lists for venue in sublist])
venues.columns = [
    'Neighborhood', 
    'Neighborhood Latitude', 
    'Neighborhood Longitude', 
    'Venue', 
    'Venue Latitude', 
    'Venue Longitude', 
    'Venue Category'
]

In [13]:
# Optional. To save Foursquare requests between executions
# venues.to_csv("venues.csv")
# venues = pd.read_csv("venues.csv", index_col=0)

In [14]:
print(venues.shape)
venues.head()

(2141, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0         Parkwoods              43.753259              -79.329656   
1         Parkwoods              43.753259              -79.329656   
2  Victoria Village              43.725882              -79.315572   
3  Victoria Village              43.725882              -79.315572   
4  Victoria Village              43.725882              -79.315572   

                    Venue  Venue Latitude  Venue Longitude  \
0         Brookbanks Park       43.751976       -79.332140   
1           Variety Store       43.751974       -79.333114   
2  Victoria Village Arena       43.723481       -79.315635   
3             Tim Hortons       43.725517       -79.313103   
4               Portugril       43.725819       -79.312785   

          Venue Category  
0                   Park  
1      Food & Drink Shop  
2           Hockey Arena  
3            Coffee Shop  
4  Portuguese Restaurant

Let's check how many venues were returned for each neighborhood

In [15]:
count = pd.DataFrame(venues.groupby("Neighborhood")["Neighborhood"].count())
count.columns = ['Count']
count.sort_values(by='Count', ascending=False)

Count
Neighborhood                                             
Toronto Dominion Centre, Design Exchange              100
Richmond, Adelaide, King                              100
Harbourfront East, Union Station, Toronto Islands     100
Garden District, Ryerson                              100
First Canadian Place, Underground city                100
Commerce Court, Victoria Hotel                        100
Stn A PO Boxes                                         96
St. James Town                                         85
Church and Wellesley                                   75
Kensington Market, Chinatown, Grange Park              74
Fairview, Henry Farm, Oriole                           70
Central Bay Street                                     68
Berczy Park                                            55
St. James Town, Cabbagetown                            48
Little Portugal, Trinity                               45
Regent Park, Harbourfront                              44
The Danforth West, Riverdale                           43
Studio District                                        37
University of Toronto, Harbord                         34
Runnymede, Swansea                                     33
Willowdale, Willowdale East                            33
Leaside                                                33
Davisville                                             33
Queen's Park, Ontario Provincial Government            33
High Park, The Junction South                          25
Thorncliffe Park                                       24
Don Mills                                              23
Brockton, Parkdale Village, Exhibition Place           23
Bedford Park, Lawrence Manor East                      22
Bathurst Manor, Wilson Heights, Downsview North        21
India Bazaar, The Beaches West                         19
The Annex, North Midtown, Yorkville                    19
North Toronto West, Lawrence Park                      18
Mimico NW, The Queensway West, South of Bloor, ...     16
Business reply mail Processing Centre, South Ce...     16
Christie                                               16
Downsview                                              16
CN Tower, King and Spadina, Railway Lands, Harb...     16
Parkdale, Roncesvalles                                 14
Summerhill West, Rathnelly, South Hill, Forest ...     14
New Toronto, Mimico South, Humber Bay Shores           14
Canada Post Gateway Processing Centre                  13
Lawrence Manor, Lawrence Heights                       13
Dufferin, Dovercourt Village                           13
Steeles West, L'Amoreaux West                          12
Clarks Corners, Tam O'Shanter, Sullivan                12
Parkview Hill, Woodbine Gardens                        11
Golden Mile, Clairlea, Oakridge                        10
South Steeles, Silverstone, Humbergate, Jamesto...     10
Davisville North                                        9
Cedarbrae                                               8
Guildwood, Morningside, West Hill                       8
Woodbine Heights                                        8
Eringate, Bloordale Gardens, Old Burnhamthorpe,...      8
Northwood Park, York University                         7
Alderwood, Long Branch                                  7
Victoria Village                                        6
Westmount                                               6
Wexford, Maryvale                                       6
Willowdale, Willowdale West                             5
Agincourt                                               5
Dorset Park, Wexford Heights, Scarborough Town ...      5
Del Ray, Mount Dennis, Keelsdale and Silverthorn        5
Humewood-Cedarvale                                      5
Glencairn                                               5
Hillcrest Village                                       5
Rosedale                                                4
Forest Hill North & West, Forest Hill Road Park   

Let's find out how many unique categories can be curated from all the returned venues

In [16]:
print('There are {} uniques categories.'.format(len(venues['Venue Category'].unique())))

There are 273 uniques categories.


### Clustering the Neighborhoods

Let's prepare the data for the clustering, by creating dummies for each category

In [17]:
# one hot encoding
toronto_dummies = pd.get_dummies(venues['Venue Category'], prefix="", prefix_sep="")
toronto_dummies["Neighborhood"]  = venues["Neighborhood"] 

# move neighborhood column to the first column
fixed_columns = [toronto_dummies.columns[-1]] + list(toronto_dummies.columns[:-1])
toronto_dummies = toronto_dummies[fixed_columns]

toronto_dummies = toronto_dummies.groupby('Neighborhood').mean().reset_index()
print(toronto_dummies.shape)
toronto_dummies.head()

(96, 273)


Neighborhood  Yoga Studio  \
0                                        Agincourt          0.0   
1                           Alderwood, Long Branch          0.0   
2  Bathurst Manor, Wilson Heights, Downsview North          0.0   
3                                  Bayview Village          0.0   
4                Bedford Park, Lawrence Manor East          0.0   

   Accessories Store  Afghan Restaurant  Airport  Airport Food Court  \
0                0.0                0.0      0.0                 0.0   
1                0.0                0.0      0.0                 0.0   
2                0.0                0.0      0.0                 0.0   
3                0.0                0.0      0.0                 0.0   
4                0.0                0.0      0.0                 0.0   

   Airport Gate  Airport Lounge  Airport Service  Airport Terminal  \
0           0.0             0.0              0.0               0.0   
1           0.0             0.0              0.0               0.0   
2           0.0             0.0              0.0               0.0   
3           0.0             0.0              0.0               0.0   
4           0.0             0.0              0.0               0.0   

   American Restaurant  Antique Shop  Aquarium  Art Gallery  Art Museum  \
0             0.000000           0.0       0.0          0.0         0.0   
1             0.000000           0.0       0.0          0.0         0.0   
2             0.000000           0.0       0.0          0.0         0.0   
3             0.000000           0.0       0.0          0.0         0.0   
4             0.045455           0.0       0.0          0.0         0.0   

   Arts & Crafts Store  Asian Restaurant  Athletics & Sports  Auto Garage  \
0                  0.0               0.0                 0.0          0.0   
1                  0.0               0.0                 0.0          0.0   
2                  0.0               0.0                 0.0          0.0   
3                  0.0               0.0                 0.0          0.0   
4                  0.0               0.0                 0.0          0.0   

   Auto Workshop  BBQ Joint  Baby Store  Bagel Shop  Bakery      Bank  Bar  \
0            0.0        0.0         0.0         0.0     0.0  0.000000  0.0   
1            0.0        0.0         0.0         0.0     0.0  0.000000  0.0   
2            0.0        0.0         0.0         0.0     0.0  0.095238  0.0   
3            0.0        0.0         0.0         0.0     0.0  0.250000  0.0   
4            0.0        0.0         0.0         0.0     0.0  0.000000  0.0   

   Baseball Field  Baseball Stadium  Basketball Stadium  Beach  \
0             0.0               0.0                 0.0    0.0   
1             0.0               0.0                 0.0    0.0   
2             0.0               0.0                 0.0    0.0   
3             0.0               0.0                 0.0    0.0   
4             0.0               0.0                 0.0    0.0   

   Bed & Breakfast  Beer Bar  Beer Store  Belgian Restaurant  Bike Shop  \
0              0.0       0.0         0.0                 0.0        0.0   
1              0.0       0.0         0.0                 0.0        0.0   
2              0.0       0.0         0.0                 0.0        0.0   
3              0.0       0.0         0.0                 0.0        0.0   
4              0.0       0.0         0.0                 0.0        0.0   

   Bistro  Boat or Ferry  Bookstore  Boutique  Brazilian Restaurant  \
0     0.0            0.0        0.0       0.0                   0.0   
1     0.0            0.0        0.0       0.0                   0.0   
2     0.0            0.0        0.0       0.0                   0.0   
3     0.0            0.0        0.0       0.0                   0.0   
4     0.0            0.0        0.0       0.0                   0.0   

   Breakfast Spot  Brewery  Bridal Shop  Bubble Tea Shop  Building  \
0             0.2      0.0     0.000000              

Running the K-Means

In [18]:
# set number of clusters
kclusters = 5

toronto_clustering = toronto_dummies.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(toronto_clustering)

Now, we add the cluster to the Neighborhood's dataframe, and group them by the cluster

In [19]:
# add clustering labels
toronto_dummies.insert(0, 'Cluster', kmeans.labels_)

In [20]:
toronto_merged = toronto_dummies.join(toronto.set_index('Neighborhood'), on='Neighborhood').reset_index(drop=True).sort_values(by="Cluster")

In [21]:
palette = sns.color_palette("colorblind", 5).as_hex()

def colorify(entry, pal):
    color = palette[entry["Cluster"]]
    return [f'background-color: {color}' for c in range(entry.shape[0])]

toronto_merged.style.apply(colorify, axis=1, args=(palette,))

Finally, let's plot each cluster on the map

In [22]:
lat_avg, lng_avg = toronto['Latitude'].mean(), toronto['Longitude'].mean()
map_toronto_clusters = folium.Map(location=[lat_avg, lng_avg], zoom_start=11)

def add_clusters_to_map(entry, palette, city_map):
    label = folium.Popup(f"{entry['Neighborhood']}, {entry['Borough']}", parse_html=True)
    folium.CircleMarker(
        [entry["Latitude"], entry["Longitude"]],
        radius=5,
        popup=label,
        color=palette[entry["Cluster"]],
        fill=True,
        fill_color=palette[entry["Cluster"]],
        fill_opacity=0.6,
        parse_html=False
    ).add_to(city_map)  

    
toronto_merged.apply(add_clusters_to_map, axis=1, args=(palette, map_toronto_clusters,))
map_toronto_clusters